In [ ]:
#!pip install transformers datasets accelerate torch torchaudio evaluate jiwer

In [1]:
import os
import json

# --- 使用者需設定的路徑 ---
audio_base_path = "dataset/TRAINGING_DATASET_1/Training_Dataset_01/audio"
annotation_file_path = "dataset/TRAINGING_DATASET_1/Training_Dataset_01/task1_answer.txt"
output_metadata_file = "prepared_metadata.jsonl" # 輸出檔案名稱
# --- 設定結束 ---

metadata = []

print(f"讀取標註檔案: {annotation_file_path}")
try:
    with open(annotation_file_path, 'r', encoding='utf-8') as f_annot:
        for line_num, line in enumerate(f_annot):
            line = line.strip()
            if not line:
                continue

            parts = line.split('\t', 1)
            if len(parts) == 2:
                filename, content = parts
                # 確保 filename 包含副檔名，如果您的標註檔中沒有，可能需要調整
                # 例如，如果 filename 是 "1000"，而實際檔案是 "1000.wav"，則需要補上
                if not filename.lower().endswith(('.wav', '.mp3', '.flac', '.opus')):
                    # 嘗試常見的音訊副檔名
                    potential_wav = os.path.join(audio_base_path, f"{filename}.wav")
                    potential_mp3 = os.path.join(audio_base_path, f"{filename}.mp3")
                    if os.path.exists(potential_wav):
                        actual_filename = f"{filename}.wav"
                    elif os.path.exists(potential_mp3):
                        actual_filename = f"{filename}.mp3"
                    else:
                        print(f"警告: 在第 {line_num+1} 行，找不到音檔 {filename} 的 .wav 或 .mp3 版本，將跳過。")
                        continue
                else:
                    actual_filename = filename

                audio_filepath = os.path.join(audio_base_path, actual_filename)

                if os.path.exists(audio_filepath):
                    metadata.append({
                        "audio_filepath": audio_filepath,
                        "text": content
                    })
                else:
                    print(f"警告: 在第 {line_num+1} 行，音檔路徑不存在: {audio_filepath} (原始檔名: {filename})，將跳過。")
            else:
                print(f"警告: 在第 {line_num+1} 行，格式不正確: '{line}'，將跳過。")

except FileNotFoundError:
    print(f"錯誤: 找不到標註檔案 {annotation_file_path} 或音訊資料夾 {audio_base_path}")
    exit()

print(f"共處理 {len(metadata)} 個有效的音檔與標註。")

print(f"寫入中介資料到: {output_metadata_file}")
with open(output_metadata_file, 'w', encoding='utf-8') as f_out:
    for item in metadata:
        f_out.write(json.dumps(item, ensure_ascii=False) + '\n')

print("中介資料檔案建立完成！")

讀取標註檔案: dataset/TRAINGING_DATASET_1/Training_Dataset_01/task1_answer.txt
共處理 1539 個有效的音檔與標註。
寫入中介資料到: prepared_metadata.jsonl
中介資料檔案建立完成！


In [2]:
from datasets import load_dataset, DatasetDict, Audio

# --- 使用者需設定的路徑 ---
metadata_file = "prepared_metadata.jsonl" # 上一步產生的檔案
# --- 設定結束 ---

# 載入資料集
print(f"從 {metadata_file} 載入資料集...")
raw_dataset = load_dataset("json", data_files=metadata_file, split="train")
print("資料集初步載入完成。")
print(raw_dataset)

# 將 'audio_filepath' 轉換為實際的音訊資料，並設定取樣率為 16kHz (Whisper 要求)
# cache=False 可以避免在處理過程中產生大型快取檔案，若您的硬碟空間充足，可以移除此參數或設為 True
# 如果您的記憶體非常大，可以考慮移除 keep_in_memory=False，讓資料載入到記憶體中以加速後續處理
# 但對於大型資料集，建議 keep_in_memory=False 避免 OOM
raw_dataset = raw_dataset.cast_column("audio_filepath", Audio(sampling_rate=16000))
# 重新命名欄位以符合 Whisper 預期 (雖然不一定嚴格要求，但好習慣)
# WhisperProcessor 會預期 'audio' 和 'sentence'/'text' 這樣的欄位名
# 我們的 'text' 欄位名已經符合，所以只需要處理 'audio_filepath'
raw_dataset = raw_dataset.rename_column("audio_filepath", "audio")

print("音訊資料轉換及欄位重命名完成。")
print(raw_dataset)
print("資料集範例:", raw_dataset[0] if len(raw_dataset) > 0 else "資料集為空")

# (選擇性) 分割訓練集和驗證集
# 如果您的資料量夠大，建議分割。這裡我們用 90% 訓練，10% 驗證。
# 如果資料量較小，可以跳過這一步，全部用於訓練，或者提供一個獨立的驗證集。
# if len(raw_dataset) > 10: # 至少要有足夠資料才能分割
#     train_test_split = raw_dataset.train_test_split(test_size=0.1, shuffle=True, seed=42)
#     dataset = DatasetDict({
#         "train": train_test_split["train"],
#         "eval": train_test_split["test"]
#     })
#     print("資料集已分割為訓練集與驗證集:")
#     print(dataset)
# else:
#     dataset = DatasetDict({"train": raw_dataset}) # 若資料太少，全部當訓練集
#     print("資料量較少，全部作為訓練集:")
#     print(dataset)

# 將所有 raw_dataset 都作為訓練集
dataset = DatasetDict({
    "train": raw_dataset
})
print("所有資料已設定為訓練集，未切分驗證集：")
print(dataset)

c:\Users\ISLAB-121\.conda\envs\aicup\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


從 prepared_metadata.jsonl 載入資料集...


Generating train split: 1539 examples [00:00, 192102.67 examples/s]


資料集初步載入完成。
Dataset({
    features: ['audio_filepath', 'text'],
    num_rows: 1539
})
音訊資料轉換及欄位重命名完成。
Dataset({
    features: ['audio', 'text'],
    num_rows: 1539
})
資料集範例: {'audio': {'path': 'dataset/TRAINGING_DATASET_1/Training_Dataset_01/audio\\19.wav', 'array': array([ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
       -4.28402927e-07,  8.09485414e-07, -2.11757379e-06]), 'sampling_rate': 16000}, 'text': 'Any overture of something that\'s kind of like a little white flag or peace offering to just get a week of peace, I\'m not talking about permanent "I\'m going to placate and cow tow to you and to talk my needs in other..." No. Just talking about lets...'}
所有資料已設定為訓練集，未切分驗證集：
DatasetDict({
    train: Dataset({
        features: ['audio', 'text'],
        num_rows: 1539
    })
})


In [3]:
from transformers import WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor, WhisperForConditionalGeneration

# --- 模型設定 ---
# 關鍵：確保使用官方標準的 Whisper 模型作為基礎，以保證特徵提取器是80維
model_name_or_path = "openai/whisper-large-v3" 
# 如果您之前是從已微調的 `./whisper-large-v3-finetuned-custom` 繼續微調，
# 且那個模型是128維的，那麼您需要從 openai/whisper-large-v3 重新開始第一次微調，
# 或者確保您載入的微調模型其 feature_extractor 配置是80維。
# 這裡我們假設是從官方 openai/whisper-large-v3 開始新的微調。

language_for_prompt = "zh" # 明確指定您的目標語言為中文
task_for_prompt = "transcribe" # 任務是轉錄
# --- 設定結束 ---

# 1. 載入 Feature Extractor
# 從 "openai/whisper-large-v3" 載入的 feature_extractor 預設就是80個Mel bins
try:
    print(f"從 '{model_name_or_path}' 載入 Feature Extractor...")
    feature_extractor = WhisperFeatureExtractor.from_pretrained(model_name_or_path)
    print(f"Feature Extractor 載入成功。Num Mel Bins: {feature_extractor.feature_size}") # 應為 80
    if feature_extractor.feature_size != 80:
        print(f"警告：Feature Extractor 的 feature_size 為 {feature_extractor.feature_size}，不是標準的80！")
        print("請確認 model_name_or_path ('{model_name_or_path}') 指向的是官方標準的 Whisper 模型，以獲得80維特徵。")
except Exception as e:
    print(f"載入 Feature Extractor 失敗: {e}")
    raise # 重新拋出異常，因為這是關鍵組件

# 2. 載入 Tokenizer
try:
    print(f"從 '{model_name_or_path}' 載入 Tokenizer...")
    tokenizer = WhisperTokenizer.from_pretrained(model_name_or_path)
    print("Tokenizer 載入成功。")
except Exception as e:
    print(f"載入 Tokenizer 失敗: {e}")
    raise

# 3. 載入 Processor
try:
    print(f"從 '{model_name_or_path}' 載入 Processor...")
    processor = WhisperProcessor.from_pretrained(model_name_or_path)
    print("Processor 載入成功。")
except Exception as e:
    print(f"載入 Processor 失敗: {e}")
    raise

# 4. 載入預訓練模型
try:
    print(f"從 '{model_name_or_path}' 載入預訓練模型...")
    model = WhisperForConditionalGeneration.from_pretrained(model_name_or_path)
    print("預訓練模型 WhisperForConditionalGeneration 載入成功。")
except Exception as e:
    print(f"載入預訓練模型失敗: {e}")
    raise

# --- 設定模型的 forced_decoder_ids 以啟用時間戳預測 ---
# 關鍵修改：no_timestamps=False
# 這會讓模型在訓練時學習預測時間戳相關的特殊 token
try:
    print(f"設定 forced_decoder_ids for language='{language_for_prompt}', task='{task_for_prompt}', no_timestamps=False")
    model.config.forced_decoder_ids = processor.get_decoder_prompt_ids(
        language=language_for_prompt, 
        task=task_for_prompt, 
        no_timestamps=False  # <--- 重要修改：設為 False 來啟用時間戳預測
    )
    # （可選）如果您不希望模型在開頭預測 <|notimestamps|> 之後立刻接時間戳（如果您的資料是這樣）
    # 您可能需要更細緻地調整 forced_decoder_ids 的內容，
    # 但通常 processor.get_decoder_prompt_ids(no_timestamps=False) 會生成合適的引導序列。
    # 例如，它會包含 <|startoftranscript|>, <|language|>, <|task|>，然後模型會學習接下來生成文本或時間戳。

    # （可選）對於 multilingual large-v3，有時需要指定 decoder_start_token_id
    # model.config.decoder_start_token_id = processor.tokenizer.bos_token_id # 通常 WhisperProcessor 會處理好
    
    print(f"模型設定 - forced_decoder_ids (啟用時間戳): {model.config.forced_decoder_ids}")
    print(f"模型設定 - suppress_tokens: {model.config.suppress_tokens}") # 通常微調時不需要更改預設的 suppress_tokens
except Exception as e:
    print(f"設定 forced_decoder_ids 失敗: {e}")
    raise

從 'openai/whisper-large-v3' 載入 Feature Extractor...
Feature Extractor 載入成功。Num Mel Bins: 128
警告：Feature Extractor 的 feature_size 為 128，不是標準的80！
請確認 model_name_or_path ('{model_name_or_path}') 指向的是官方標準的 Whisper 模型，以獲得80維特徵。
從 'openai/whisper-large-v3' 載入 Tokenizer...
Tokenizer 載入成功。
從 'openai/whisper-large-v3' 載入 Processor...
Processor 載入成功。
從 'openai/whisper-large-v3' 載入預訓練模型...
預訓練模型 WhisperForConditionalGeneration 載入成功。
設定 forced_decoder_ids for language='zh', task='transcribe', no_timestamps=False
模型設定 - forced_decoder_ids (啟用時間戳): [(1, 50260), (2, 50360)]
模型設定 - suppress_tokens: None


In [4]:
def prepare_dataset(batch, processor, language="zh", task="transcribe", train_with_timestamps=True): # 新增 train_with_timestamps 參數
    # train_with_timestamps: 如果為 True (預設)，則不添加 <|notimestamps|>，讓模型學習時間戳
    #                       如果為 False，則添加 <|notimestamps|>，模型不學習時間戳
    
    # 1. 處理音訊: 提取 input_features
    audio_sample = batch["audio"]
    batch["input_features"] = processor.feature_extractor(
        audio_sample["array"],
        sampling_rate=audio_sample["sampling_rate"]
    ).input_features[0] # feature_extractor 應返回80維的特徵

    # 2. 處理文本: token化標籤，並加入特殊 token
    lang_token = f"<|{language}|>"
    task_token = f"<|{task}|>"
    
    # 根據是否訓練時間戳來決定是否加入 <|notimestamps|> token
    if train_with_timestamps:
        # 我們要訓練模型預測時間戳，所以不應在目標文本中明確加入 <|notimestamps|>
        # decoder 的起始序列 (由 forced_decoder_ids 控制) 已經不包含 <|notimestamps|> 了
        no_timestamps_token_str = "" 
    else:
        # 如果由於某些原因，這次微調仍然不希望預測時間戳
        no_timestamps_token_str = "<|notimestamps|>"
    
    # 構造的目標文本，tokenizer 會自動處理 BOS (<|startoftranscript|>) 和 EOS (<|endoftext|>)
    formatted_text_for_labels = f"{lang_token}{task_token}{no_timestamps_token_str}{batch['text']}"
    
    batch["labels"] = processor.tokenizer(text_target=formatted_text_for_labels, return_attention_mask=False).input_ids
    return batch

In [5]:
from functools import partial

# 關鍵修改：將 train_with_timestamps 設為 True (或不傳遞 no_timestamps_in_prompt，使其使用 prepare_dataset 中的預設值)
prepare_dataset_fn = partial(prepare_dataset, 
                             processor=processor, 
                             language=language_for_prompt, # 使用 Cell 3 中定義的 language_for_prompt
                             task=task_for_prompt,         # 使用 Cell 3 中定義的 task_for_prompt
                             train_with_timestamps=True    # <--- 重要修改
                            )

print("開始預處理資料集...")
processed_dataset = dataset.map(
    prepare_dataset_fn,
    remove_columns=dataset["train"].column_names,
    num_proc=1 
)
print("資料集預處理完成。")
print(processed_dataset)
print("處理後訓練集範例:", processed_dataset["train"][0] if len(processed_dataset["train"]) > 0 else "訓練集為空")
# ... (後續打印 eval 範例的部分不變) ...
if "eval" in processed_dataset and len(processed_dataset["eval"]) > 0 : # 檢查 eval 是否存在且不為空
    print("處理後驗證集範例:", processed_dataset["eval"][0])

開始預處理資料集...


Map: 100%|██████████| 1539/1539 [01:59<00:00, 12.84 examples/s]

資料集預處理完成。
DatasetDict({
    train: Dataset({
        features: ['input_features', 'labels'],
        num_rows: 1539
    })
})
處理後訓練集範例: {'input_features': [[-0.784165620803833, -0.784165620803833, -0.784165620803833, -0.784165620803833, -0.784165620803833, -0.739399790763855, -0.22159409523010254, -0.2809256315231323, -0.37210166454315186, -0.32740938663482666, -0.2757216691970825, -0.4350297451019287, -0.33236968517303467, -0.1946110725402832, -0.3691587448120117, -0.10835719108581543, -0.04118633270263672, -0.13625335693359375, -0.03944230079650879, 0.04555058479309082, -0.05647468566894531, -0.24768352508544922, -0.019732356071472168, -0.1064155101776123, -0.20226800441741943, -0.39217817783355713, -0.11357581615447998, -0.12648022174835205, -0.2036736011505127, -0.24399936199188232, -0.26059627532958984, -0.3849886655807495, -0.3944333791732788, -0.5458599328994751, -0.468029260635376, -0.16488981246948242, -0.18611693382263184, -0.43420660495758057, -0.4710209369659424, -0.5578685

In [6]:
import torch
from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class CustomDataCollatorSpeechSeq2SeqWithPadding:
    processor: Any  # 通常是 WhisperProcessor 或類似的物件，包含 tokenizer 和 feature_extractor

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        """
        將預處理過的特徵列表（來自 dataset.map(prepare_dataset)）組合成一個批次。

        Args:
            features (List[Dict[str, Union[List[int], torch.Tensor]]]):
                一個字典的列表，每個字典代表一個樣本，且應包含：
                - "input_features": 已經由 feature_extractor 處理過的音訊特徵 (例如，一個 2D numpy array 或 tensor)。
                - "labels": 已經由 tokenizer 處理過的目標文字 token ID 序列 (例如，一個 1D numpy array 或 tensor)。
                                這些 labels 應該已經包含了所有必要的特殊 token（如語言、任務、BOS/EOS token）。
        Returns:
            Dict[str, torch.Tensor]: 一個包含批次化張量的字典，用於模型訓練。
                                     至少應包含 "input_features", "labels", "decoder_input_ids"。
                                     可能還包含 "attention_mask" (用於 encoder 的 input_features)。
        """

        # 1. 處理音訊特徵 (input_features)
        #    將 "input_features" 從每個樣本中取出，然後使用 feature_extractor 的 .pad() 方法進行填充和批次化。
        #    `WhisperFeatureExtractor` 類別（通常是 processor.feature_extractor）有一個 .pad() 方法。
        input_features_list_of_dicts = [{"input_features": feature["input_features"]} for feature in features]
        
        # 使用 feature_extractor.pad 進行填充，它會處理填充到批次中最長序列，並返回 PyTorch 張量
        # 同時，如果 feature_extractor 支持，它也會返回 attention_mask
        padded_input_features_obj = self.processor.feature_extractor.pad(
            input_features_list_of_dicts,
            padding=True,        # 填充到批次中的最大長度
            return_tensors="pt", # 返回 PyTorch 張量
        )
        batch_input_features = padded_input_features_obj["input_features"]


        # 2. 處理文字標籤 (labels)
        #    將 "labels" 從每個樣本中取出，然後使用 tokenizer 的 .pad() 方法進行填充和批次化。
        #    填充時，被填充的 token ID 會被設置為 -100，這樣在計算損失時它們會被忽略。
        labels_list_of_dicts = [{"input_ids": feature["labels"]} for feature in features]

        # 使用 tokenizer.pad 進行填充
        padded_labels_obj = self.processor.tokenizer.pad(
            labels_list_of_dicts,
            padding=True,        # 填充到批次中的最大長度
            return_tensors="pt", # 返回 PyTorch 張量
        )
        labels = padded_labels_obj["input_ids"]

        # 將 labels 中由 tokenizer.pad_token_id 填充的部分替換為 -100
        # 這是為了讓損失函數忽略這些填充的 token
        labels_pad_token_mask = labels.eq(self.processor.tokenizer.pad_token_id)
        labels[labels_pad_token_mask] = -100


        # 3. 建立解碼器輸入 (decoder_input_ids)
        #    `decoder_input_ids` 是將 `labels` 向右平移一位，並在開頭加上解碼器開始符號得到的。
        #    對於 Whisper，`prepare_dataset` 函數處理 `formatted_text` 時，
        #    `tokenizer` 會自動在 tokenized `labels` 的最前面加上 BOS token (通常是 <|startoftranscript|> for Whisper)。
        #    我們需要確保 `decoder_input_ids` 的第一個 token 是這個 BOS token。

        # 先複製一份 labels (在被 -100 替換填充值之前的版本，如果需要的話，但這裡用已替換的也可以，因為之後會處理)
        # 確保 decoder_input_ids 中的填充是 tokenizer.pad_token_id 而不是 -100
        decoder_input_ids = labels.clone()
        decoder_input_ids[decoder_input_ids == -100] = self.processor.tokenizer.pad_token_id

        # 向右平移
        # shifted_decoder_input_ids 的第一個位置將是填充值 (例如 self.processor.tokenizer.pad_token_id)
        # 其他位置是 decoder_input_ids 的 [:, :-1]
        shifted_decoder_input_ids = decoder_input_ids.new_zeros(decoder_input_ids.shape) # 創建一個全零張量
        shifted_decoder_input_ids[..., 1:] = decoder_input_ids[..., :-1].clone()

        # 將 shifted_decoder_input_ids 的第一個 token 設置為解碼器開始符號
        # 對於 Whisper，這通常是 tokenizer.bos_token_id (<|startoftranscript|>)
        # 模型的 `config.forced_decoder_ids` 會在 `generate` 時處理後續的語言和任務 token。
        # 在訓練時，decoder_input_ids 的起始序列應該是模型期望看到的。
        # 如果 labels 的第一個 token 就是 BOS (<|startoftranscript|>)，那麼平移後，
        # shifted_decoder_input_ids 的第二個位置就會是這個 BOS。
        # 我們需要將第一個位置明確設為 BOS。
        if self.processor.tokenizer.bos_token_id is None:
            raise ValueError("Processor's tokenizer must have a bos_token_id set.")
        shifted_decoder_input_ids[..., 0] = self.processor.tokenizer.bos_token_id
        
        # 準備返回的字典
        batch = {
            "input_features": batch_input_features,
            "labels": labels,
            "decoder_input_ids": shifted_decoder_input_ids,
        }

        # 如果 feature_extractor.pad 返回了 attention_mask (針對 encoder)，也將其加入 batch
        if "attention_mask" in padded_input_features_obj:
            batch["attention_mask"] = padded_input_features_obj["attention_mask"]
            
        return batch

In [7]:
import torch
# 實例化自訂的 data collator
custom_data_collator = CustomDataCollatorSpeechSeq2SeqWithPadding(processor=processor)

# DataCollator 會動態地將 input_features 和 labels 填充到批次中的最大長度
# processor 包含了 feature_extractor (處理 input_features 的填充) 和 tokenizer (處理 labels 的填充)
data_collator=custom_data_collator
print("Data Collator 初始化完成。")

Data Collator 初始化完成。


In [8]:
import evaluate

# 載入 WER 指標
try:
    wer_metric = evaluate.load("wer")
    print("WER 評估指標載入成功。")
except Exception as e:
    print(f"載入 WER 指標失敗: {e}")
    print("請嘗試執行: pip install evaluate jiwer")
    exit()

def compute_metrics(pred):
    # pred 是一個 EvalPrediction 物件，包含 predictions 和 label_ids
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # 將 label_ids 中的 -100 (用於填充的 token) 替換為 pad_token_id，以便解碼
    # 因為 tokenizer 在解碼時不應處理 -100
    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    # 解碼預測的 token ID 和真實的 token ID 為文本
    # skip_special_tokens=True 會移除 <|startoftranscript|>, <|endoftext|> 等特殊 token
    pred_str = processor.batch_decode(pred_ids, skip_special_tokens=True, normalize=True)
    label_str = processor.batch_decode(label_ids, skip_special_tokens=True, normalize=True)

    # 計算 WER
    # 我們需要確保 pred_str 和 label_str 是 list of strings
    # batch_decode 返回的就是 list of strings
    wer = wer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

WER 評估指標載入成功。


In [9]:
from transformers import Seq2SeqTrainingArguments

# --- 訓練參數設定 ---
output_dir = "./whisper-large-v3-finetuned-custom-with-timestamps" # <<-- 建議改個新目錄名
per_device_train_batch_size = 2 
per_device_eval_batch_size = 2
gradient_accumulation_steps = 3
learning_rate = 1e-5 
warmup_steps = 500
num_train_epochs = 2 # 您設為2，如果資料量大，可能需要更多，或用 max_steps

eval_strategy = "no" # 您已設為 "no"
# eval_steps = 1000 # 在 eval_strategy="no" 時無效
save_strategy = "steps" # <<-- 如果 eval_strategy="no"，保存策略設為 "epoch" 或 "steps" 更合適
save_steps = 1000 # 如果 save_strategy="steps"，此參數有效
logging_steps = 500 

fp16 = torch.cuda.is_available()
# --- 以下為可選但建議的調整 ---
load_best_model_at_end = False # <<-- 如果 eval_strategy="no"，則無法判斷最佳模型，應設為 False
metric_for_best_model = None   # <<-- 相應地，這個也應為 None 或移除
# greater_is_better = False    # <<-- 也無關了
# --- 調整結束 ---

training_args = Seq2SeqTrainingArguments(
    output_dir=output_dir,
    per_device_train_batch_size=per_device_train_batch_size,
    per_device_eval_batch_size=per_device_eval_batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    learning_rate=learning_rate,
    warmup_steps=warmup_steps,
    num_train_epochs=num_train_epochs,
    
    evaluation_strategy=eval_strategy,
    # eval_steps=eval_steps, # 若 evaluation_strategy="no"，此行可註解

    save_strategy=save_strategy, # 使用您選擇的保存策略
    # save_steps=save_steps, # 若 save_strategy="steps"，則此參數需要
    # save_total_limit=2, # 例如，只保留最新的2個 checkpoints

    logging_steps=logging_steps,
    fp16=fp16,
    
    load_best_model_at_end=load_best_model_at_end, # 修改後的值
    # metric_for_best_model=metric_for_best_model, # 可註解或移除
    # greater_is_better=greater_is_better,       # 可註解或移除
    
    # predict_with_generate=True, # 對於 Seq2Seq Trainer 通常是 True，即使不評估，保留也無妨
                                # 但如果嚴格不需要，可以考慮移除或設為 False，但建議保留
    
    # 如果您在訓練過程中，希望看到模型生成的一些範例輸出（即使不進行正式評估）
    # 可以將 predict_with_generate 設為 True。
    # 這不會影響訓練本身，但如果 compute_metrics 被意外調用，它能確保正常運作。
    # 考慮到 Whisper 微調通常會用到，建議保留或明確設為 True。
    predict_with_generate=True,


    push_to_hub=False,
    remove_unused_columns=False, 
    report_to=["tensorboard"],
)

print("訓練參數 TrainingArguments 初始化完成。")

訓練參數 TrainingArguments 初始化完成。


c:\Users\ISLAB-121\.conda\envs\aicup\lib\site-packages\transformers\training_args.py:1575: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [11]:
from transformers import Seq2SeqTrainer

# 建立 Trainer
trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=processed_dataset["train"],
    eval_dataset=processed_dataset.get("eval"), # 使用 .get 以防 "eval" 不存在
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor, # 重要：Trainer 需要 tokenizer 來填充 input_features，這裡傳 feature_extractor
                                         # 因為 DataCollatorSpeechSeq2SeqWithPadding 內部會用 processor.tokenizer 處理 labels
                                         # 並且 feature_extractor 的 pad_token_id (如果有的話) 也會被 data_collator 用於 input_features
                                         # 實際上，Seq2SeqTrainer 期望 tokenizer 參數用於填充輸入和解碼預測。
                                         # 給予 processor (其中包含 tokenizer 和 feature_extractor) 通常是安全的。
                                         # 或者更準確地說，是 processor.tokenizer。
                                         # DataCollator 用 processor 處理，但 Trainer 的 tokenizer 參數用於評估時解碼。
)
# processor.save_pretrained(training_args.output_dir) # 也可以先保存 processor

print("Seq2SeqTrainer 初始化完成。準備開始訓練...")

# --- 開始訓練 ---
try:
    print("開始訓練...")
    train_result = trainer.train()
    print("訓練完成！")

    # 保存訓練結果的指標
    metrics = train_result.metrics
    trainer.log_metrics("train", metrics)
    trainer.save_metrics("train", metrics)

    # 保存最終的模型和 processor
    print(f"保存最終模型到 {training_args.output_dir}")
    trainer.save_model() # 這會保存模型、訓練參數等
    # 也保存 processor，方便後續載入
    processor.save_pretrained(training_args.output_dir)
    print("模型和 Processor 保存完成。")

except Exception as e:
    print(f"訓練過程中發生錯誤: {e}")
    import traceback
    traceback.print_exc()

# (選擇性) 如果有驗證集，可以在訓練後進行一次最終評估
if processed_dataset.get("eval"):
    print("在驗證集上進行最終評估...")
    eval_metrics = trainer.evaluate(eval_dataset=processed_dataset["eval"])
    trainer.log_metrics("eval_final", eval_metrics)
    trainer.save_metrics("eval_final", eval_metrics)
    print("最終評估完成。")

C:\Users\ISLAB-121\AppData\Local\Temp\ipykernel_16860\960548809.py:4: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Seq2SeqTrainer.__init__`. Use `processing_class` instead.
  trainer = Seq2SeqTrainer(


Seq2SeqTrainer 初始化完成。準備開始訓練...
開始訓練...


Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.43.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.


c:\Users\ISLAB-121\.conda\envs\aicup\lib\site-packages\transformers\modeling_utils.py:2758: UserWarning: Moving the following attributes in the config to the generation config: {'max_length': 448, 'begin_suppress_tokens': [220, 50257]}. You are seeing this warning because you've set generation parameters in the model config, as opposed to in the generation config.
  warnings.warn(


訓練完成！
***** train metrics *****
  epoch                    =       1.9935
  total_flos               = 9710828124GF
  train_loss               =       0.3728
  train_runtime            =   0:28:02.00
  train_samples_per_second =         1.83
  train_steps_per_second   =        0.304
保存最終模型到 ./whisper-large-v3-finetuned-custom-with-timestamps
模型和 Processor 保存完成。


In [ ]:
import os
import glob
from transformers import WhisperForConditionalGeneration, WhisperProcessor, pipeline
import torch
import whisperx # 主要用於 audio 載入、對齊模型載入、對齊功能
import time

# --- 使用者需設定的路徑 ---
# ↓↓↓↓↓↓ 請將此路徑更新為您「新」微調模型的儲存路徑 ↓↓↓↓↓↓
hf_model_path = "./whisper-large-v3-finetuned-custom-with-timestamps"  # <<--- 更新此處！
# 例如，如果您在微調腳本的 TrainingArguments 中設定的 output_dir 是這個，就用這個。

audio_dir = "dataset/TRAINGING_DATASET_1/Validation_Dataset/audio"  # 驗證集音訊檔案夾
output_no_timestamps_file = "transcriptions_no_timestamps.txt" # 建議新檔名
output_word_timestamps_file = "transcriptions_word_timestamps_aligned.txt" # 建議新檔名

# --- 推論設定 ---
# 給 Hugging Face Pipeline 的 generate_kwargs
# 由於模型已微調且配置已清理，這裡主要設定重複懲罰等。
hf_pipeline_generate_kwargs = {
    "repetition_penalty": 1.2,
    "no_repeat_ngram_size": 3
    # 如果您的 transformers 版本較舊 (例如 4.36.2)，且清除了模型配置中的 language/task 後，
    # 模型仍無法正確識別語言或任務，您可能需要在此處重新加入：
    # "language": "zh",
    # "task": "transcribe",
    # 但通常對於已針對特定語言微調的模型，在清除了 baked-in config 後，它應能自行處理。
}

# WhisperX 對齊設定
whisperx_align_language_code = "zh" # 對齊模型的語言代碼
# --- 設定結束 ---

def format_whisperx_word_segments(word_segments):
    """將 WhisperX align 後的 word_segments 格式化為 word[start-end] 的字串"""
    output_str_list = []
    if not word_segments:
        return ""
    for segment in word_segments:
        word = segment.get('word', '').strip()
        start_time = segment.get('start')
        end_time = segment.get('end')

        if word and start_time is not None and end_time is not None:
            st_str = f"{start_time:.2f}"
            et_str = f"{end_time:.2f}"
            output_str_list.append(f"{word}[{st_str}-{et_str}]")
        elif word: 
            output_str_list.append(word) # 即使沒有時間戳，也保留單詞
            
    return " ".join(output_str_list)

def main():
    print("開始進行音訊轉錄 (使用新微調的模型)...")
    start_total_time = time.time()

    # --- 1. 設備偵測 ---
    if torch.cuda.is_available():
        device = "cuda"
        hf_pipeline_device = 0
        print(f"CUDA 可用。將使用 GPU: {torch.cuda.get_device_name(0)}")
    else:
        device = "cpu"
        hf_pipeline_device = -1
        print("CUDA 不可用。將使用 CPU。")

    # --- 2. 載入 Hugging Face Processor 和新微調的模型 ---
    print(f"\n正在從 '{hf_model_path}' 載入 Processor 和新微調的模型...")
    asr_pipeline = None
    loaded_model_hf = None # 確保在 try 外部可以被後續引用 (雖然目前只在 try 內部使用)
    loaded_processor_hf = None

    try:
        loaded_processor_hf = WhisperProcessor.from_pretrained(hf_model_path)
        loaded_model_hf = WhisperForConditionalGeneration.from_pretrained(hf_model_path)
        
        # --- 清除可能衝突的模型配置 (仍然建議保留此步驟) ---
        print(f"HF 模型原始 config.forced_decoder_ids: {getattr(loaded_model_hf.config, 'forced_decoder_ids', 'N/A')}")
        loaded_model_hf.config.forced_decoder_ids = None
        
        original_suppress_tokens = None # 用於恢復
        if hasattr(loaded_model_hf.config, 'suppress_tokens'):
            original_suppress_tokens = loaded_model_hf.config.suppress_tokens # 保存原始設定
            print(f"HF 模型原始 config.suppress_tokens: {original_suppress_tokens}")
            # loaded_model_hf.config.suppress_tokens = [] # 微調時不應隨意清空，除非確定影響生成
        
        if hasattr(loaded_model_hf.config, 'begin_suppress_tokens'):
             print(f"HF 模型原始 config.begin_suppress_tokens: {loaded_model_hf.config.begin_suppress_tokens}")
            # loaded_model_hf.config.begin_suppress_tokens = []

        # 清除 language 和 task，讓模型依賴微調結果，並由 generate_kwargs 控制（如果需要）
        if hasattr(loaded_model_hf.config, 'language'):
            print(f"HF 模型原始 config.language: {loaded_model_hf.config.language}")
            loaded_model_hf.config.language = None
        if hasattr(loaded_model_hf.config, 'task'):
            print(f"HF 模型原始 config.task: {loaded_model_hf.config.task}")
            loaded_model_hf.config.task = None

        # 檢查 feature_size 是否為 80 (標準)
        if hasattr(loaded_processor_hf.feature_extractor, 'feature_size'):
            print(f"HF 模型 Feature Extractor feature_size: {loaded_processor_hf.feature_extractor.feature_size}")
            if loaded_processor_hf.feature_extractor.feature_size != 80:
                print(f"警告：新微調模型的 feature_size 為 {loaded_processor_hf.feature_extractor.feature_size}，而非標準的 80。")
                print("這可能會影響與期望80維特徵的工具（如某些WhisperX後端）的兼容性。")
        print(f"HF 模型清除後 config.forced_decoder_ids: {getattr(loaded_model_hf.config, 'forced_decoder_ids', 'N/A')}")
        # --- 清除配置結束 ---

        loaded_model_hf.to(device).eval()
        print("Hugging Face 新微調模型和 Processor 載入並配置完成。")

        asr_pipeline = pipeline(
            "automatic-speech-recognition",
            model=loaded_model_hf,
            tokenizer=loaded_processor_hf.tokenizer,
            feature_extractor=loaded_processor_hf.feature_extractor,
            device=hf_pipeline_device,
            chunk_length_s=30,
            stride_length_s=[5,0] 
        )
        print("ASR Pipeline 建立完成。")
    except Exception as e:
        print(f"建立 ASR Pipeline 或載入/配置新微調模型失敗: {e}")
        import traceback
        traceback.print_exc()
        return

    # --- 3. 載入 WhisperX 對齊模型 ---
    model_align = None
    metadata_align = None
    if not os.path.exists(audio_dir):
        print(f"音訊目錄 '{audio_dir}' 不存在。程式終止。")
        return
    try:
        print(f"\n正在載入 WhisperX 的語言對齊模型: {whisperx_align_language_code}...")
        model_align, metadata_align = whisperx.load_align_model(
            language_code=whisperx_align_language_code, device=device 
        )
        print("WhisperX 對齊模型載入成功。")
    except Exception as e:
        print(f"載入 WhisperX 對齊模型失敗: {e}")
        print("警告：詞時間戳對齊功能可能無法使用。")
        import traceback
        traceback.print_exc()

    # --- 4. 遍歷音訊檔案並進行處理 ---
    audio_files = []
    for ext in ("*.wav", "*.mp3", "*.flac", "*.opus", "*.m4a"):
        audio_files.extend(glob.glob(os.path.join(audio_dir, ext)))

    if not audio_files:
        print(f"在 '{audio_dir}' 中找不到任何音訊檔案。請檢查路徑。")
        return
        
    print(f"\n找到 {len(audio_files)} 個音訊檔案，開始處理...")
    transcriptions_no_ts_list = []
    transcriptions_word_ts_list = []

    for i, audio_path in enumerate(audio_files):
        filename = os.path.basename(audio_path)
        print(f"\n處理檔案 ({i+1}/{len(audio_files)}): {filename}")
        file_start_time = time.time()
        current_transcription_text = "ERROR_TRANSCRIPTION_HF_PIPELINE_FAILED"
        hf_pipeline_segments_for_alignment = []

        try:
            # === A. 產生無時間戳的轉錄稿 (使用 Hugging Face Pipeline) ===
            print("  使用 Hugging Face Pipeline 進行轉錄 (無時間戳)...")
            # hf_pipeline_generate_kwargs 應只包含 repetition_penalty 等，不含 language/task
            result_no_ts = asr_pipeline(audio_path, generate_kwargs=hf_pipeline_generate_kwargs)
            current_transcription_text = result_no_ts["text"].strip()
            transcriptions_no_ts_list.append(f"{filename}\t{current_transcription_text}\n")
            print(f"    無時間戳轉錄 (來自 HF Pipeline): {current_transcription_text[:100]}...")

            # === B. 產生帶詞時間戳的轉錄稿 (直接從 Hugging Face Pipeline 獲取) ===
            print("  嘗試使用 Hugging Face Pipeline 直接獲取詞級時間戳...")
            # 移除所有 WhisperX ASR 和 align 的相關程式碼，直接使用 HF pipeline
            
            # 再次確認 hf_pipeline_generate_kwargs 不包含可能衝突的參數
            # 並且確保模型的 config 已被正確清理
            result_word_ts_hf = asr_pipeline(
                audio_path,
                return_timestamps="word", # <--- 關鍵修改：請求詞級時間戳
                generate_kwargs=hf_pipeline_generate_kwargs 
            )
            
            if "chunks" in result_word_ts_hf and result_word_ts_hf["chunks"]:
                # result_word_ts_hf["chunks"] 的格式應為:
                # [{'text': '詞1', 'timestamp': (開始1, 結束1)}, {'text': '詞2', 'timestamp': (開始2, 結束2)}, ...]
                
                # 使用您之前定義的 format_hf_pipeline_word_chunks 函數 (如果已定義)
                # 或者我們在這裡直接格式化：
                formatted_ts_text_list = []
                for chunk_idx, chunk_word in enumerate(result_word_ts_hf["chunks"]):
                    if isinstance(chunk_word, dict) and "text" in chunk_word and "timestamp" in chunk_word and \
                       isinstance(chunk_word["timestamp"], (tuple, list)) and len(chunk_word["timestamp"]) == 2:
                        
                        word_text = chunk_word["text"].strip() # Whisper常在詞前後產生空格
                        start_time, end_time = chunk_word["timestamp"]

                        if word_text and start_time is not None and end_time is not None:
                            st_str = f"{start_time:.2f}"
                            et_str = f"{end_time:.2f}"
                            formatted_ts_text_list.append(f"{word_text}[{st_str}-{et_str}]")
                        else:
                            print(f"    警告: HF Pipeline (word) 返回的 chunk {chunk_idx} 缺少有效時間戳或文本，跳過: {chunk_word}")
                    else:
                        print(f"    警告: HF Pipeline (word) 返回的 chunk {chunk_idx} 格式不正確，跳過: {chunk_word}")
                
                if formatted_ts_text_list:
                    formatted_ts_text = " ".join(formatted_ts_text_list)
                    transcriptions_word_ts_list.append(f"{filename}\t{formatted_ts_text}\n")
                    print(f"    詞時間戳轉錄 (直接來自 HF Pipeline): {formatted_ts_text[:100]}...")
                else:
                    print(f"    HF Pipeline 未能為 {filename} 生成有效的詞級時間戳內容。使用無時間戳文本。")
                    transcriptions_word_ts_list.append(f"{filename}\t{current_transcription_text} # HF Pipeline 無有效詞時間戳內容\n")
            else:
                print(f"    HF Pipeline (請求詞時間戳 'word' 時) 未返回 'chunks' 或 'chunks' 為空 for {filename}。使用無時間戳文本。")
                transcriptions_word_ts_list.append(f"{filename}\t{current_transcription_text} # HF Pipeline 無詞時間戳 chunks\n")

        except Exception as e_file_processing:
            print(f"  處理檔案 {filename} 時發生嚴重錯誤: {e_file_processing}")
            import traceback
            traceback.print_exc()
            if len(transcriptions_no_ts_list) == i:
                 transcriptions_no_ts_list.append(f"{filename}\tERROR_PROCESSING_FILE\n")
            if len(transcriptions_word_ts_list) == i:
                 transcriptions_word_ts_list.append(f"{filename}\tERROR_PROCESSING_FILE\n")
        
        file_end_time = time.time()
        print(f"  檔案處理耗時: {file_end_time - file_start_time:.2f} 秒")

    # --- 5. 寫入結果到檔案 ---
    try:
        with open(output_no_timestamps_file, "w", encoding="utf-8") as f:
            for line in transcriptions_no_ts_list:
                f.write(line)
        print(f"\n無時間戳轉錄結果已儲存到: {output_no_timestamps_file}")
    except Exception as e:
        print(f"儲存無時間戳轉錄結果失敗: {e}")

    if model_align and metadata_align:
        try:
            with open(output_word_timestamps_file, "w", encoding="utf-8") as f:
                for line in transcriptions_word_ts_list:
                    f.write(line)
            print(f"帶詞時間戳轉錄結果 (嘗試來自 HF Pipeline) 已儲存到: {output_word_timestamps_file}")
        except Exception as e:
            print(f"儲存帶詞時間戳轉錄結果失敗: {e}")
            
    end_total_time = time.time()
    print(f"\n所有檔案處理完成，總耗時: {(end_total_time - start_total_time) / 60:.2f} 分鐘")

if __name__ == "__main__":
    main()

c:\Users\ISLAB-121\.conda\envs\aicup\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


開始進行音訊轉錄 (使用新微調的模型)...
CUDA 可用。將使用 GPU: NVIDIA RTX 6000 Ada Generation

正在從 './whisper-large-v3-finetuned-custom-with-timestamps' 載入 Processor 和新微調的模型...


Loading checkpoint shards: 100%|██████████| 2/2 [00:00<00:00,  3.76it/s]


HF 模型原始 config.forced_decoder_ids: [[1, 50260], [2, 50360]]
HF 模型原始 config.suppress_tokens: None
HF 模型原始 config.begin_suppress_tokens: None
HF 模型 Feature Extractor feature_size: 128
警告：新微調模型的 feature_size 為 128，而非標準的 80。
這可能會影響與期望80維特徵的工具（如某些WhisperX後端）的兼容性。
HF 模型清除後 config.forced_decoder_ids: None


Device set to use cuda:0


...

Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.43.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


    無時間戳轉錄 (來自 HF Pipeline): Right. And you sort of... You want him to take responsibility for the, for the things that he's doin...
  嘗試使用 Hugging Face Pipeline 直接獲取詞級時間戳...


WhisperModel is using WhisperSdpaAttention, but `torch.nn.functional.scaled_dot_product_attention` does not support `output_attentions=True` or `layer_head_mask` not None. Falling back to the manual attention implementation, but specifying the manual implementation will be required from Transformers version v5.0.0 onwards. This warning can be removed using the argument `attn_implementation="eager"` when loading the model.
From v4.47 onwards, when a model cache is to be returned, `generate` will return a `Cache` instance instead by default (as opposed to the legacy tuple of tuples format). If you want to keep returning the legacy format, please set `return_legacy_cache=True`.
Whisper did not predict an ending timestamp, which can happen if audio is cut off in the middle of a word. Also make sure WhisperTimeStampLogitsProcessor was used during generation.


    警告: HF Pipeline (word) 返回的 chunk 89 缺少有效時間戳或文本，跳過: {'text': ' am.', 'timestamp': (26.4, None)}
    詞時間戳轉錄 (直接來自 HF Pipeline): Right.[0.00-0.34] And[0.34-0.74] you[0.74-0.84] sort[0.84-1.06] of[1.06-1.34] ...[1.34-1.36] You[1.3...
  檔案處理耗時: 13.99 秒

處理檔案 (2/775): 24018.wav
  使用 Hugging Face Pipeline 進行轉錄 (無時間戳)...
    無時間戳轉錄 (來自 HF Pipeline): I said, ’You know it’s not really your field and even if it was you are his dad and you are so close...
  嘗試使用 Hugging Face Pipeline 直接獲取詞級時間戳...


KeyboardInterrupt: 